<a href="https://colab.research.google.com/github/balwanishivam/Sentiment-Analysis/blob/main/LSTM.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
import numpy as np 
import pandas as pd 
import nltk
import re
from nltk.corpus import stopwords
from bs4 import BeautifulSoup    
from sklearn.metrics import accuracy_score
nltk.download('stopwords')
from collections import Counter
import matplotlib.pyplot as plt
import torch
from torch.utils.data import DataLoader, TensorDataset

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [2]:
def text_cleaning(texts):
    clean_text = []
    for text in texts:
        text = BeautifulSoup(text, "lxml").get_text() 
        text = re.sub("[^a-zA-Z]", " ", text) 
        text = text.lower().split('\n')                            
        clean_text.append((" ".join(text)))
    return clean_text

In [3]:
train = pd.read_csv("labeledTrainData.tsv", header=0, delimiter="\t", quoting=3)
print(train.head(5))
print("Train shape:", train.shape)
print("Train set sentiment ratio:\n", train.sentiment.value_counts(dropna=False))
X = text_cleaning(train['review'])
print(X[1])
print ('Number of reviews :', len(X)) 
y=train['sentiment'] 

         id  sentiment                                             review
0  "5814_8"          1  "With all this stuff going down at the moment ...
1  "2381_9"          1  "\"The Classic War of the Worlds\" by Timothy ...
2  "7759_3"          0  "The film starts with a manager (Nicholas Bell...
3  "3630_4"          0  "It must be assumed that those who praised thi...
4  "9495_8"          1  "Superbly trashy and wondrously unpretentious ...
Train shape: (25000, 3)
Train set sentiment ratio:
 1    12500
0    12500
Name: sentiment, dtype: int64
   the classic war of the worlds   by timothy hines is a very entertaining film that obviously goes to great effort and lengths to faithfully recreate h  g  wells  classic book  mr  hines succeeds in doing so  i  and those who watched his film with me  appreciated the fact that it was not the standard  predictable hollywood fare that comes out every year  e g  the spielberg version with tom cruise that had only the slightest resemblance to the book

In [4]:
print("Creating World List")
all_text = ' '.join(X)
words = all_text.split()
count_words = Counter(words)
total_words = len(words)
sorted_words = count_words.most_common(total_words)
print("Word List Created")

Creating World List
Word List Created


In [5]:
print (count_words)

Counter({'the': 336653, 'and': 164113, 'a': 163138, 'of': 145855, 'to': 135705, 'is': 107318, 'it': 96445, 'in': 93960, 'i': 87645, 'this': 75968, 'that': 73276, 's': 66086, 'was': 48198, 'as': 46937, 'for': 44335, 'with': 44121, 'movie': 44031, 'but': 42615, 'film': 40147, 't': 34402, 'you': 34261, 'on': 34202, 'not': 30629, 'he': 30144, 'are': 29432, 'his': 29369, 'have': 27726, 'be': 26953, 'one': 26788, 'all': 23976, 'at': 23510, 'they': 22908, 'by': 22543, 'an': 21562, 'who': 21437, 'so': 20611, 'from': 20494, 'like': 20274, 'there': 18857, 'her': 18419, 'or': 18005, 'just': 17767, 'about': 17372, 'out': 17109, 'if': 16799, 'has': 16786, 'what': 16166, 'some': 15744, 'good': 15140, 'can': 14672, 'more': 14247, 'she': 14223, 'when': 14178, 'very': 14066, 'up': 13291, 'time': 12724, 'no': 12722, 'even': 12646, 'my': 12490, 'would': 12436, 'which': 12051, 'story': 11983, 'only': 11915, 'really': 11736, 'see': 11475, 'their': 11381, 'had': 11289, 'we': 10860, 'were': 10784, 'me': 1077

In [6]:
vocab_to_int = {w:i+1 for i, (w,c) in enumerate(sorted_words)}
print (vocab_to_int)
reviews_int = []
print(X[0])
for review in X:
    r = [vocab_to_int[w] for w in review.split()]
    reviews_int.append(r)
print (reviews_int[0:5])
# print(np.array(reviews_int).shape)

{'the': 1, 'and': 2, 'a': 3, 'of': 4, 'to': 5, 'is': 6, 'it': 7, 'in': 8, 'i': 9, 'this': 10, 'that': 11, 's': 12, 'was': 13, 'as': 14, 'for': 15, 'with': 16, 'movie': 17, 'but': 18, 'film': 19, 't': 20, 'you': 21, 'on': 22, 'not': 23, 'he': 24, 'are': 25, 'his': 26, 'have': 27, 'be': 28, 'one': 29, 'all': 30, 'at': 31, 'they': 32, 'by': 33, 'an': 34, 'who': 35, 'so': 36, 'from': 37, 'like': 38, 'there': 39, 'her': 40, 'or': 41, 'just': 42, 'about': 43, 'out': 44, 'if': 45, 'has': 46, 'what': 47, 'some': 48, 'good': 49, 'can': 50, 'more': 51, 'she': 52, 'when': 53, 'very': 54, 'up': 55, 'time': 56, 'no': 57, 'even': 58, 'my': 59, 'would': 60, 'which': 61, 'story': 62, 'only': 63, 'really': 64, 'see': 65, 'their': 66, 'had': 67, 'we': 68, 'were': 69, 'me': 70, 'well': 71, 'than': 72, 'much': 73, 'get': 74, 'bad': 75, 'been': 76, 'people': 77, 'will': 78, 'do': 79, 'other': 80, 'also': 81, 'into': 82, 'first': 83, 'great': 84, 'because': 85, 'how': 86, 'him': 87, 'don': 88, 'most': 89, '

In [7]:
reviews_len = [len(x) for x in reviews_int]
pd.Series(reviews_len).hist()
plt.show()
pd.Series(reviews_len).describe()

count    25000.000000
mean       236.828520
std        175.999818
min         10.000000
25%        129.000000
50%        177.000000
75%        287.000000
max       2487.000000
dtype: float64

In [8]:
def pad_features(reviews_int, seq_length):
    # Return features of review_ints, where each review is padded with 0's or truncated to the input seq_length.
    features = np.zeros((len(reviews_int), seq_length), dtype = int)
    
    for i, review in enumerate(reviews_int):
        review_len = len(review)
        
        if review_len <= seq_length:
            zeroes = list(np.zeros(seq_length-review_len))
            new = zeroes+review
        elif review_len > seq_length:
            new = review[0:seq_length]
        
        features[i,:] = np.array(new)
    
    return features

In [9]:
features=pad_features(reviews_int,200)
print (features[:10,:])

[[  16   30   10 ... 3457 1639  703]
 [   0    0    0 ...   28   91 5614]
 [   1   19  505 ...    1   62 1540]
 ...
 [   0    0    0 ...    6   10  365]
 [   0    0    0 ...    4   30   56]
 [   0    0    0 ...    8    1  682]]


In [10]:
split_frac = 0.8
len_feat=len(features)
train_x = features[0:int(split_frac*len_feat)]
train_y = y[0:int(split_frac*len_feat)]
remaining_x = features[int(split_frac*len_feat):]
remaining_y = y[int(split_frac*len_feat):]
valid_x = remaining_x[0:int(len(remaining_x)*0.5)]
valid_y = remaining_y[0:int(len(remaining_y)*0.5)]
test_x = remaining_x[int(len(remaining_x)*0.5):]
test_y = remaining_y[int(len(remaining_y)*0.5):]

In [11]:
train_data = TensorDataset(torch.from_numpy(np.array(train_x)), torch.from_numpy(np.array(train_y)))
valid_data = TensorDataset(torch.from_numpy(np.array(valid_x)), torch.from_numpy(np.array(valid_y)))
test_data = TensorDataset(torch.from_numpy(np.array(test_x)), torch.from_numpy(np.array(test_y)))
batch_size = 50
train_loader = DataLoader(train_data, shuffle=True, batch_size=batch_size)
valid_loader = DataLoader(valid_data, shuffle=True, batch_size=batch_size)
test_loader = DataLoader(test_data, shuffle=True, batch_size=batch_size)

In [12]:
dataiter = iter(train_loader)
sample_x, sample_y = dataiter.next()
print('Sample input size: ', sample_x.size()) 
print('Sample input: \n', sample_x)
print()
print('Sample label size: ', sample_y.size()) 
print('Sample label: \n', sample_y)

Sample input size:  torch.Size([50, 200])
Sample input: 
 tensor([[    0,     0,     0,  ...,    12,   445,    63],
        [    0,     0,     0,  ...,    23,    97,    49],
        [    0,     0,     0,  ...,    98,    44,    39],
        ...,
        [    0,     0,     0,  ...,     2,    49,   306],
        [    1, 17927,     6,  ...,  4228,     3,   169],
        [    0,     0,     0,  ...,    82,     1,   491]])

Sample label size:  torch.Size([50])
Sample label: 
 tensor([0, 0, 1, 1, 0, 1, 0, 1, 0, 1, 1, 0, 1, 1, 1, 0, 1, 0, 0, 1, 0, 0, 0, 1,
        1, 1, 0, 1, 1, 0, 1, 1, 1, 1, 1, 0, 0, 0, 0, 0, 0, 0, 1, 1, 0, 1, 1, 1,
        0, 1])


In [13]:
import torch.nn as nn

class SentimentLSTM(nn.Module):
    """
    The RNN model that will be used to perform Sentiment analysis.
    """

    def __init__(self, vocab_size, output_size, embedding_dim, hidden_dim, n_layers, drop_prob=0.5):
        """
        Initialize the model by setting up the layers.
        """
        super().__init__()

        self.output_size = output_size
        self.n_layers = n_layers
        self.hidden_dim = hidden_dim
        self.embedding = nn.Embedding(vocab_size, embedding_dim)
        self.lstm = nn.LSTM(embedding_dim, hidden_dim, n_layers, dropout=drop_prob, batch_first=True)
        self.dropout = nn.Dropout(0.3)
        self.fc = nn.Linear(hidden_dim, output_size)
        self.sig = nn.Sigmoid()
        

    def forward(self, x, hidden):
        """
        Perform a forward pass of our model on some input and hidden state.
        """
        batch_size = x.size(0)
        embeds = self.embedding(x)
        lstm_out, hidden = self.lstm(embeds, hidden)
        lstm_out = lstm_out.contiguous().view(-1, self.hidden_dim)
        out = self.dropout(lstm_out)
        out = self.fc(out)
        sig_out = self.sig(out)
        sig_out = sig_out.view(batch_size, -1)
        sig_out = sig_out[:, -1]
        return sig_out, hidden
    
    
    def init_hidden(self, batch_size):
        ''' Initializes hidden state '''
        weight = next(self.parameters()).data
        hidden = (weight.new(self.n_layers, batch_size, self.hidden_dim).zero_(),weight.new(self.n_layers, batch_size, self.hidden_dim).zero_())
        return hidden

In [14]:
# Instantiate the model w/ hyperparams
vocab_size = len(vocab_to_int)+1 # +1 for the 0 padding
output_size = 1
embedding_dim = 400
hidden_dim = 256
n_layers = 2
net = SentimentLSTM(vocab_size, output_size, embedding_dim, hidden_dim, n_layers)
print(net)

SentimentLSTM(
  (embedding): Embedding(74219, 400)
  (lstm): LSTM(400, 256, num_layers=2, batch_first=True, dropout=0.5)
  (dropout): Dropout(p=0.3, inplace=False)
  (fc): Linear(in_features=256, out_features=1, bias=True)
  (sig): Sigmoid()
)


In [15]:
lr=0.001
criterion = nn.BCELoss()
optimizer = torch.optim.Adam(net.parameters(), lr=lr)
epochs = 4

counter = 0
print_every = 100
clip=5 # gradient clipping

net.train()
for e in range(epochs):
    print("Epoch started")
    # initialize hidden state
    h = net.init_hidden(batch_size)

    # batch loop
    for inputs, labels in train_loader:
        counter += 1
        # Creating new variables for the hidden state, otherwise
        # we'd backprop through the entire training history
        h = tuple([each.data for each in h])

        # zero accumulated gradients
        net.zero_grad()

        # get the output from the model
        inputs = inputs.type(torch.LongTensor)
        output, h = net(inputs, h)

        # calculate the loss and perform backprop
        loss = criterion(output.squeeze(), labels.float())
        loss.backward()
        # `clip_grad_norm` helps prevent the exploding gradient problem in RNNs / LSTMs.
        nn.utils.clip_grad_norm_(net.parameters(), clip)
        optimizer.step()

        # loss stats
        if counter % print_every == 0:
            # Get validation loss
            val_h = net.init_hidden(batch_size)
            val_losses = []
            net.eval()
            for inputs, labels in valid_loader:
                # Creating new variables for the hidden state, otherwise
                # we'd backprop through the entire training history
                val_h = tuple([each.data for each in val_h])
                inputs = inputs.type(torch.LongTensor)
                output, val_h = net(inputs, val_h)
                val_loss = criterion(output.squeeze(), labels.float())

                val_losses.append(val_loss.item())

            net.train()
            print("Epoch: {}/{}...".format(e+1, epochs),
                  "Step: {}...".format(counter),
                  "Loss: {:.6f}...".format(loss.item()),
                  "Val Loss: {:.6f}".format(np.mean(val_losses)))

Epoch started
Epoch: 1/4... Step: 100... Loss: 0.650094... Val Loss: 0.686327
Epoch: 1/4... Step: 200... Loss: 0.598346... Val Loss: 0.619500
Epoch: 1/4... Step: 300... Loss: 0.596838... Val Loss: 0.611334
Epoch: 1/4... Step: 400... Loss: 0.652206... Val Loss: 0.544137
Epoch started
Epoch: 2/4... Step: 500... Loss: 0.361625... Val Loss: 0.495943
Epoch: 2/4... Step: 600... Loss: 0.533350... Val Loss: 0.525166
Epoch: 2/4... Step: 700... Loss: 0.514619... Val Loss: 0.456010
Epoch: 2/4... Step: 800... Loss: 0.310338... Val Loss: 0.422248
Epoch started
Epoch: 3/4... Step: 900... Loss: 0.431864... Val Loss: 0.433203
Epoch: 3/4... Step: 1000... Loss: 0.403037... Val Loss: 0.458799
Epoch: 3/4... Step: 1100... Loss: 0.324241... Val Loss: 0.414049
Epoch: 3/4... Step: 1200... Loss: 0.231668... Val Loss: 0.405086
Epoch started
Epoch: 4/4... Step: 1300... Loss: 0.187524... Val Loss: 0.450015
Epoch: 4/4... Step: 1400... Loss: 0.428722... Val Loss: 0.465208
Epoch: 4/4... Step: 1500... Loss: 0.224240.

In [57]:
test_losses = [] # track loss
num_correct = 0

# init hidden state
h = net.init_hidden(batch_size)

net.eval()
# iterate over test data
for inputs, labels in test_loader:

    # Creating new variables for the hidden state, otherwise
    # we'd backprop through the entire training history
    h = tuple([each.data for each in h])
    
    # get predicted outputs
    inputs = inputs.type(torch.LongTensor)
    output, h = net(inputs, h)
    
    # calculate loss
    test_loss = criterion(output.squeeze(), labels.float())
    test_losses.append(test_loss.item())
    
    # convert output probabilities to predicted class (0 or 1)
    pred = torch.round(output.squeeze())  # rounds to the nearest integer
    
    # compare predictions to true label
    correct_tensor = pred.eq(labels.float().view_as(pred))
    correct = np.squeeze(correct_tensor.numpy())
    num_correct += np.sum(correct)


# -- stats! -- ##
# avg test loss
print("Test loss: {:.3f}".format(np.mean(test_losses)))

# accuracy over all test data
test_acc = num_correct/len(test_loader.dataset)
print("Test accuracy: {:.3f}".format(test_acc*100))

Test loss: 0.407
Test accuracy: 84.440


In [51]:
from string import punctuation

def tokenize_review(test_review):
    test_review = test_review.lower() # lowercase
    # get rid of punctuation
    test_text = ''.join([c for c in test_review if c not in punctuation])

    # splitting by spaces
    test_words = test_text.split()

    # tokens
    test_ints = []
    for word in test_words:
      value=vocab_to_int.get(word,0)
      if value ==0:    
        vocab_to_int[word]=value
    test_ints.append([vocab_to_int[word] for word in test_words])
    # print(([vocab_to_int[word] for word in test_words]))

    return test_ints


def predict(net, test_review, sequence_length=200):
    
    net.eval()
    
    # tokenize review
    test_ints = tokenize_review(test_review)
    
    # pad tokenized sequence
    seq_length=sequence_length
    features = pad_features(test_ints, seq_length)
    
    # convert to tensor to pass into your model
    feature_tensor = torch.from_numpy(features)
    
    batch_size = feature_tensor.size(0)
    
    # initialize hidden state
    h = net.init_hidden(batch_size)
    
    
    # get the output from the model
    output, h = net(feature_tensor, h)
    
    # convert output probabilities to predicted class (0 or 1)
    pred = torch.round(output.squeeze()) 
    # printing output value, before rounding
    print('Prediction value, pre-rounding: {:.6f}'.format(output.item()))
    
    # print custom response
    if(pred.item()==1):
        print("Positive review detected!")
    else:
        print("Negative review detected.")

In [53]:
test_review = 'This movie had the best acting and the dialogue was so good. I loved it.'
seq_length=200 # good to use the length that was trained on
test_ints = tokenize_review(test_review)
# print(test_ints)
# for i, review in enumerate(test_ints):
#   print(review)
#   print(i)
#   print(len(review))
predict(net, test_review, seq_length)

Prediction value, pre-rounding: 0.994860
Positive review detected!


In [55]:
test = pd.read_csv("testData.tsv", header=0, delimiter="\t", quoting=3)
x_test=test['review']
for review in x_test:
  print(review)
  predict(net,review)

Streaming output truncated to the last 5000 lines.
Prediction value, pre-rounding: 0.977324
Positive review detected!
"The director infuses this film with false depth by repeating a gimmick throughout the film. EVERY single shot in this movie is 3 times longer than it needs to be. You could easily cut out 1.5 hours of this agonizingly long 2.5 hour film without eliminating: one word of dialogue, one image, one event, or bit of movement.<br /><br />This was one of the most gratuitous wastes of film I have ever seen. Other reviewers have called it pretentious, which is an understatement. L'Humanite is pseudo-intellectual trash designed to be anti-Hollywood so that the Cannes judges could assert their independence from the Oscars.<br /><br />The IMDb reviewer states: \"Unlike Hollywood movies - which usually force the audience into overdrive - this forces the audience to slow down and look at some of life's tiniest and most mundane features in great detail.\" You would have to be catatoni